In [ ]:
import numpy as np
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import random as rand
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
%matplotlib qt
%config InlineBackend.figure_format = 'retina'

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Meteorite Impact Calculator', artist='Iain',comment='')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [ ]:
## Constants
g = 9.81 #acceleration of gravity in m/s
r = 6378100 #radius of the earth in m
thermosphere = 600000 #Outer layer of atmosphere with very trace amounts of oxygen: 600,000 m to 85,000m
mesosphere = 85000 # altitude of the mesosphere (where smaller meteors tend to burn up) 85,000 m to 50,000m
#stratosphere is between troposphere and mesophere
troposphere = 14000 # ~altitude of the troposphere, lowest layer, where weather occurs. Varies depending on latitude

z = thermosphere #Sets initial altitude of meteor visibility would depend on size

In [ ]:
print(z)

In [ ]:
#Meteor conditions
v_chi = 50000 #magnitude of velocity in m/s. Chicxulub estimated from 20km/s to 70km/s
mass_chi = 1e16 #estimated mass of Chicxulub from 1e15 to 4.6e17 kg
diameter_chi = 10000 #estimated diameter of Chicxulub in meters

theta_deg = 35.0 #want to calculate a roughly 35 degree impact but then favor dx over dy

# Convert the angle to radians
theta_rad = np.radians(theta_deg)


v_initial = v_chi 

# Calculate the horizontal velocity in the xy-plane
v_horizontal = v_initial * np.cos(theta_rad)

# Calculate the velocity in the z direction (altitude)
#dz = v_initial * np.sin(theta_rad)

# Calculate dx and dy favoring dx
#dx = v_horizontal*2/3
#dy = v_horizontal*1/3

#Used made up numbers instead for more interesting animation
dx = 20000
dy = 8000
dz = 1500

#Randomly select direction of travel
#if rand.choice([True, False]):
#    dx = abs(dx)
#else:
#    dx = -abs(dx)
    
#if rand.choice([True, False]):
#    dy = abs(dy)
#else:
#    dy = -abs(dy)
#v_total = v_chi

velocity_vector = np.array([dx, dy, dz])

# Calculate the magnitude of the initial velocity vector
v_initial = np.linalg.norm(velocity_vector)
print('total velocity is now: ',v_initial)
# Calculate the horizontal velocity in the xy-plane
v_horizontal = np.linalg.norm(velocity_vector[:2])

# Calculate the angle of impact in radians then degrees
theta_rad = np.arccos(v_horizontal / v_initial)
theta_deg = np.degrees(theta_rad)


print('The angle of impact is ',theta_deg,' degrees.')
print('The velocity components are:')
print('dx=',dx)
print('dy=',dy)
print('dz=',dz)

In [ ]:
a = g
b = abs(dz)
c = -1 * z
discriminant = b**2 - 4*a*c

# Calculate the two solutions
t1 = (-b + np.sqrt(discriminant)) / (2*a)
t2 = (-b - np.sqrt(discriminant)) / (2*a)


if t1 > 0:
    total_time = t1
else:
    total_time = t2
    
print(total_time)

n = 50 #number of steps
dt = total_time/n
print(dt)

In [ ]:
# Create a figure with Mollweide projection
fig = plt.figure(figsize=(50, 30))
ax = fig.add_subplot(1, 1, 1, projection=ccrs.Mollweide(central_longitude=0))

# Set the extent of the map to show the entire globe
ax.set_global()

# Add coastlines , gridlines, country borders, and color in land and ocean
ax.coastlines(resolution='10m', color='gray')
ax.gridlines()
ax.add_feature(cfeature.BORDERS)
ax.add_feature(cfeature.LAND, color = 'green')
ax.add_feature(cfeature.OCEAN)


height_text = plt.text(0.95, 0.01, '', transform=ax.transAxes, fontsize=25, verticalalignment='bottom', horizontalalignment='right', bbox=dict(facecolor='white', alpha=0.5))
info_text = plt.text(0.95, 0.95, '', transform=ax.transAxes, fontsize=15, verticalalignment='top', horizontalalignment='right', bbox=dict(facecolor='white', alpha=0.5))

#start_lat,start_lon = 40.785105, -73.857556
start_lat,start_lon = 8.639935, 15.222339
#start_lat = rand.uniform(-90.0000,90.0000)
start_lat = round(start_lat,4)
#start_lon = rand.uniform(-180.0000,180.0000)
start_lon = round(start_lon,4)

print('The meteorite initally enters the atmosphere at',start_lat,' degrees latitude and ')
print(start_lon,' degrees longitude')
print(start_lat,',',start_lon)

lat = np.copy(start_lat)
lon = np.copy(start_lon)

q=0
lonmap=[]
latmap=[]
endlon=[]
endlat=[]


onelat=(2*np.pi*r)/360 #1 degree change in latitude [m]

with writer.saving(fig, "animation2.mp4" , dpi=200):
    while z>0:
        height_text.set_text(f'Current altitude of meteor: {z:.2f} meters')
        info_text.set_text(f'Current coordinates: {lat:.2f}, {lon:.2f}')


        onelon=(np.pi*r*np.cos(np.radians(abs(lat))))/180 #1 degree change in long [m]

        lat_change=dy *dt /onelat #change in latitude converted to degrees
        lon_change=dx *dt /onelon #change in longitude converted to degrees

        # Update velocities
        dz += g * dt

        #Update longitude and latitude and set boundary conditions
        lat += lat_change
        lon += lon_change
        if lat > 90:
            remainder = lat-90
            lat = -90 + remainder
            lonmap=[]
            latmap=[]
        if lat < -90:
            remainder = lat+90
            lat = 90 + remainder
            lonmap=[]
            latmap=[]
        if lon > 180:
            remainder = lon - 180
            lon = -180 + remainder
            lonmap=[]
            latmap=[]
        if lon < -180:
            remainder = lon + 180
            lon = 180 + remainder
            lonmap=[]
            latmap=[]
        else:
            lonmap.append(lon)
            latmap.append(lat)

        print('coordinates of meteorite are: ',lat,',',lon)
        print('Current height is ',z, 'meters')

            

       


        ax.plot(lonmap , latmap , color='red', linewidth=1, marker='o', transform=ccrs.PlateCarree())
        
        writer.grab_frame()
        z -= dz *dt #step the altitude of the meteor
        if z<0:
            endlon = lon
            endlat = lat
        q+=1
        print('q is: ',q)

        # Display the plot
        plt.draw()
        plt.pause(0.1)
        
    
    ax.plot(endlon, endlat, marker='*', color='blue', markersize=10, transform=ccrs.PlateCarree())
    height_text.set_text('Height 0.00 meters')
    #plt.show()
    for i in range(75):
        writer.grab_frame()

In [ ]:
print(endlon,endlat)